# 1. Introduction

## 1.1 Zillow Prize

The [Zillow Prize](https://www.zillow.com/promo/Zillow-prize/) is a data science and machine learning competition organized by the [Zillow real estate company](https://www.zillow.com/). 
The competition is host by [Kaggle](https://www.kaggle.com/), a company that provides datasets and computational kernels for data science challenges, which was [purchased by Google](https://techcrunch.com/2017/03/07/google-is-acquiring-data-science-community-kaggle/) earlier this year. 
The Zillow Prize competition has recently declared to be the [second largest data science challenge on Kaggle](https://www.prnewswire.com/news-releases/zillow-prize-ranks-as-one-of-most-popular-machine-learning-contests-of-all-time-300539347.html).
The purpose of the Zillow prize is to inspire data scientists around the world to work on improving the accuracy of the Zillow "Zestimate" home price estimate algorithm.

## 1.2 Zillow Zestimate home valuation algorithm

Zillow’s Zestimate home valuation was first released in 2006 and has since had a major impact on the United States real estate industry. The Zestimate algorithm created a new standard of providing free, publicly available housing data and home price estimates. 
The Zestimate algorithm relies on ["7.5 million statistical and machine learning models"](https://www.prnewswire.com/news-releases/zillow-prize-ranks-as-one-of-most-popular-machine-learning-contests-of-all-time-300539347.html) that have been refined over the years to have a [margin of error on only 5%](https://www.kaggle.com/c/zillow-prize-1).

The real estate industry is a major contributor to the U.S economy and was worth roughly [30 trillion dollars in 2016](https://www.zillow.com/research/2016-total-home-value-rents-14028/). Homeownership equity is a major form of wealth that Americans hold, while mortgages are a major type of American private debt. It is extremely important for U.S. homeowners and for the U.S. economy that home prices are estimated correctly. Without proper estimates, lender and borrowers cannot confidently monitor their assets and liabilities. Overevaluation of real estate assets and the potential returns on real estate debt for lenders has been linked to the great recession. <cite data-cite="5251998/GKWP3DLG"></cite> 

# 2. Methods

## 2.1 Data

The data provided for the Zillow challenge were 2016 and 2017 datasets consisting of XXX features and XXX observations. The total size of the data was XXX MB. "The first rule of large data is to make it into small data" quote. To make the data easier to work with, I first removed features consisting of more than 60% missing values (Supplemental Figure S1). 
I then used median imputation to fill in the missing values for the remaining features.
Next, I used two prediction methods: Random Forest and XGBoost to obtain importance scores for each of the remaining features (Figure 1). I also compared the Random Forest importance scores to the importance scores obtained using the Extra Trees Regression method (Supplemental Figure 2). I removed features that had an importance of less than 0.001 from both of the tree based models and an F score importance of less than 10. Of the initial XXX features, now XX features remained. 

The data were obtained from [Kaggle website](https://www.kaggle.com/c/zillow-prize-1/data) and consist of the following files:

- properties_2016.csv.zip
- properties_2017.csv.zip
- sample_submission.csv
- train_2016_v2.csv.zip
- train_2017.csv.zip
- zillow_data_dictionary.xlsx

The `zillow_data_dictionary.xlsx` is a code book that explains the data.
This data will be made available on [figshare](https://figshare.com/) to provide an additional source if the [Kaggle site data](https://www.kaggle.com/c/zillow-prize-1/data) become unavailable.

## Analysis

Data analysis was done in Jupyter Notebook (formerly known as IPython Notebook) <cite data-cite="5251998/SH25XT8L"></cite> Integrated Development Environment using the Python language <cite data-cite="5251998/FGTD82L2"></cite> and a number of software packages:

- NumPy <cite data-cite="5251998/3SWILWGR"></cite>
- Pandas <cite data-cite="5251998/K3NZPGU9"></cite>
- Scikit-learn (Pedregosa et al. 2011)


## Visualization

The following packages were used to visualize the data:

- Matplotlib <cite data-cite="5251998/WP5LZ6AZ"></cite>
- Seaborn 


## Prediction

Machine learning prediction was done using the following packages:

- scikit-learn (Pedregosa et al. 2011)
- xgboost
- r-caret 

### Reproducibility

Reproducibility is extremely important in scientific research yet many examples of problematic studies exist in the literature (Couzin-Frankel 2010)<cite data-cite="5251998/UXR4ZTUS"></cite>.

The names and versions of each package used herein are listed in the accompanying `env.yml` file in the `config` folder.
The computational environment used to analyze the data can be recreated using this `env.yml` file and the [`conda` package and environment manager](https://conda.io/docs/using/envs.html) available as part of the [Anaconda distribution of Python](https://www.anaconda.com/download/).

Additionally, details on how to setup a Docker image capable of running the analysis is included in the `README.md` file in the `config` folder.

The code in the form of a jupyter notebook (`01_zillow_MWS.ipynb`) or Python script (`01_zillow_MWS.py`), can also be run on the Kaggle website (this requires logging in with a username and password).

More information on the details of how this project was created and the computational environment was configured can be found in the accompanying `README.md` file.

This Python 3 environment comes with many helpful analytics libraries installed
It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python (a modified version of this docker image will be made available as part of my project to ensure reproducibility).
For example, here's several helpful packages to load in 

# Results

There are several columns which have a very high proportion of missing values. I will remove features that have more than 80% missing values.

In [145]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import matplotlib.pyplot as plt # data visualization
import seaborn as sns
import xgboost as xgb
from sklearn.preprocessing import LabelEncoder
from sklearn.ensemble import RandomForestRegressor
from sklearn.ensemble import ExtraTreesRegressor

In [4]:
# Set plot parameters
from IPython.display import set_matplotlib_formats

plt.rcParams['savefig.dpi'] = 300

%matplotlib inline
### Seaborn style
sns.set_style("whitegrid")

In [5]:
#Input data files are available in the "../input/" directory, on Kaggle and this repo.
prop = pd.read_csv("../input/properties_2016.csv", low_memory=False)
prop.shape;

In [6]:
### ... check for NaNs
nan = prop.isnull().sum()/len(prop)*100

In [7]:
### Plotting NaN counts
nan_sorted = nan.sort_values(ascending=False).to_frame().reset_index()
nan_sorted.columns = ['Column', 'percentNaN']
nan_sorted.head();

In [61]:
train = pd.read_csv("../input/train_2016_v2.csv", parse_dates=["transactiondate"])
train.shape;

In [62]:
train['transaction_month'] = pd.DatetimeIndex(train['transactiondate']).month
train.sort_values('transaction_month', axis=0, ascending=True, inplace=True)

In [63]:
#fill NaN values with -1 and encode object columns 
for x in prop.columns:
    prop[x] = prop[x].fillna(-1)

#many more parcelids in properties file, merge with training file
train = pd.merge(train, prop, on='parcelid', how='left')


In [64]:
for c in train[['transactiondate', 'hashottuborspa', 'propertycountylandusecode', 'propertyzoningdesc', 'fireplaceflag', 'taxdelinquencyflag']]:
    label = LabelEncoder()
    label.fit(list(train[c].values))
    train[c] = label.transform(list(train[c].values))

x_train = train.drop(['parcelid', 'logerror', 'transactiondate'], axis=1)
y_train = train['logerror']

## Feature Importance by Random Forest and Xgboost

In [66]:
rf = RandomForestRegressor(n_estimators=30, max_features=None)
rf.fit(x_train, y_train);

In [67]:
rf_importance = rf.feature_importances_
rf_importance_df = pd.DataFrame()
rf_importance_df['features'] = x_train.columns
rf_importance_df['importance'] = rf_importance
rf_importance_df.head();

In [68]:
rf_importance_df.sort_values('importance', axis=0, inplace=True, ascending=False)

rf_importance_df_trim = rf_importance_df[rf_importance_df.importance>0.001]

rf_importance_df_trim.tail()

rf_feature_list = rf_importance_df_trim.features

In [78]:
xgb_params = {
    'eta': 0.05,
    'max_depth': 8,
    'subsample': 0.7,
    'colsample_bytree': 0.7,
    'objective': 'reg:linear',
    'silent': 1,
    'seed' : 0
}
dtrain = xgb.DMatrix(x_train, y_train, feature_names=x_train.columns.values)
model = xgb.train(dict(xgb_params, silent=0), dtrain, num_boost_round=50)

In [ ]:
xgbdict = model.get_score()

xgb_importance_df = pd.DataFrame()
xgb_importance_df['features'] = xgbdict.keys()
xgb_importance_df['importance'] = xgbdict.values()

xgb_importance_df.sort_values('importance', axis=0, inplace=True, ascending=False)

xgb_importance_df_trim = xgb_importance_df[xgb_importance_df.importance>=10]

xgb_feature_list = xgb_importance_df_trim.features

feature_list = xgb_feature_list.append(rf_feature_list)

feature_list = feature_list.unique()

feature_list

In [147]:
# Create  a 1 x 2 grid of subplots
num_rows = 1
num_cols = 2

fig = plt.figure(figsize=(200, 256))
plt.subplots_adjust(wspace=1)


sns.set_context("poster", font_scale=10)
# [1]
ax = plt.subplot2grid((num_rows, num_cols), (0,0))
sns.barplot(x="importance", y="features", data=rf_importance_df, color='Green', ax=ax)
ax.set(xlabel="Importance", ylabel="")
ax.set_title('Random Forest Importance', fontsize= 165)
# [2]
ax = plt.subplot2grid((num_rows, num_cols), (0,1))
xgb.plot_importance(model, height=0.8, grid = False, color="blue", ax=ax)
ax.xaxis.grid()
ax.set_title('XGBoost Importance', fontsize= 165)
ax.set(xlabel="Importance (F score)", ylabel="")
plt.show()

# Conclusions

In Progress

In [ ]:
# Bibliography is added in post-processing

<div class="cite2c-biblio"></div>